In [1]:
import folium
from folium.plugins import HeatMap
import pandas as pd
import numpy as np
from argparse import ArgumentParser
import time           #Para obtener tiempo del sistema
import datetime       #Para operaciones con tiempos
import matplotlib.pyplot as plt
plt.style.use('ggplot')

In [2]:
start = time.time()
hurtos_moto = pd.read_csv(r'https://raw.githubusercontent.com/jaarciah/Proyecto-Integrador-2020-periodo-2/master/Data/Preprocessing/hurto_motos_dummy_ingCaracteristicas.csv', sep = ";").copy()
#comunas_med = pd.read_csv('comunas_med.csv', sep = ";").copy()
#hurtos_moto = pd.read_csv('hurto_de_moto.csv', sep = ";").copy()
#comunas_med = pd.read_csv('comunas_med.csv', sep = ";").copy()
hurtos_moto['fecha_hecho'] = hurtos_moto['fecha_hecho'].astype('datetime64')
hurtos_moto.info()
end = time.time()
print("El tiempo que tomó en leer el archivo {}".format((end-start)))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 64109 entries, 0 to 64108
Data columns (total 24 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   fecha_hecho       64109 non-null  datetime64[ns]
 1   latitud           64109 non-null  float64       
 2   longitud          64109 non-null  float64       
 3   estado_civil      64109 non-null  int64         
 4   medio_transporte  64109 non-null  int64         
 5   modalidad         64109 non-null  int64         
 6   arma_medio        64109 non-null  int64         
 7   nombre_barrio     64109 non-null  int64         
 8   codigo_comuna     64109 non-null  int64         
 9   lugar             64109 non-null  int64         
 10  sede_receptora    64109 non-null  int64         
 11  modelo            64109 non-null  int64         
 12  fecha             64109 non-null  object        
 13  anho              64109 non-null  int64         
 14  mes               6410

In [3]:
hurtos_moto['year'] =  hurtos_moto.fecha_hecho.apply(lambda x: x.year)
hurtos_moto['month'] =  hurtos_moto.fecha_hecho.apply(lambda x: x.month)
hurtos_moto['week'] =  hurtos_moto.fecha_hecho.apply(lambda x: x.week)
hurtos_moto['day'] =  hurtos_moto.fecha_hecho.apply(lambda x: x.day)
hurtos_moto['hour'] =  hurtos_moto.fecha_hecho.apply(lambda x: x.hour)
hurtos_moto['year_month'] = hurtos_moto.fecha_hecho.apply(lambda x: x.year*100+x.month)
hurtos_moto['year_month_week'] = hurtos_moto.fecha_hecho.apply(lambda x: x.year*10000+x.month*100+x.week)
hurtos_moto['year_month_day'] = hurtos_moto.fecha_hecho.apply(lambda x: x.year*10000+x.month*100+x.day)
hurtos_moto['year_month_day_hour'] = hurtos_moto.fecha_hecho.apply(lambda x: x.year*1000000+x.month*10000+x.day*100+x.hour)
hurtos_moto['cantidad'] = 1 
#hurtos_moto['year_month'] =  hurtos_moto.fecha_hecho.str.slice(0, 7)
#hurtos_moto['year_month'] =  hurtos_moto.fecha_hecho.str.replace('-','').astype('int')


In [4]:
#Eliminar Nulos
print(f'Before dropping NaNs\t:\tcluster.shape = {hurtos_moto.shape}')
hurtos_moto.dropna(inplace=True)
#cluster.drop_duplicates(subset=['LON', 'LAT'], keep='first', inplace=True)
print(f'After dropping NaNs\t:\tcluster.shape = {hurtos_moto.shape}')

Before dropping NaNs	:	cluster.shape = (64109, 34)
After dropping NaNs	:	cluster.shape = (64109, 34)


In [ ]:
hurtos_moto.head()

In [5]:
def generateBaseMap(default_location=[hurtos_moto.latitud.median(), hurtos_moto.longitud.median()], default_zoom_start=11.5):
    base_map = folium.Map(location=default_location, control_scale=True, zoom_start=default_zoom_start)
    return base_map

In [6]:
base_map = generateBaseMap()
base_map

In [7]:
from folium.plugins import HeatMap
df_copy = hurtos_moto.copy()

In [24]:
base_map = generateBaseMap()
m = HeatMap(data=hurtos_moto[['latitud', 'longitud', 'cantidad']].groupby(['latitud','longitud']).sum().reset_index().values.tolist(), radius=7, max_zoom=13).add_to(base_map)

In [25]:
base_map

In [ ]:
base_map.add_child(folium.ClickForMarker(popup='Potential Location'))

In [26]:
df_year_list = []
for year in df_copy.year.sort_values().unique():
    df_year_list.append(df_copy.loc[df_copy.year == year, ['latitud', 'longitud', 'cantidad']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist())

In [31]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=12)
HeatMapWithTime(df_year_list, radius=12, gradient={0.25: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.2, max_opacity=0.4, use_local_extrema=True).add_to(base_map)
base_map

In [34]:
base_map.save('HeatMap.html')

In [32]:
df_year_month_list = []
for year in df_copy.year_month.sort_values().unique():
    df_year_month_list.append(df_copy.loc[df_copy.year_month == year, ['latitud', 'longitud', 'cantidad']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist())

In [33]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=12)
HeatMapWithTime(df_year_month_list, radius=12, gradient={0.1: 'blue', 0.3: 'lime', 0.5: 'orange', 1: 'red'}, min_opacity=0.2, max_opacity=0.4, use_local_extrema=True).add_to(base_map)
base_map

In [ ]:
df_month_list = []
for month in df_copy.month.sort_values().unique():
    df_month_list.append(df_copy.loc[df_copy.month == month, ['latitud', 'longitud', 'cantidad']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist())

In [ ]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=12)
HeatMapWithTime(df_month_list, radius=5, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.5, max_opacity=0.8, use_local_extrema=True).add_to(base_map)
base_map

In [ ]:
df_day_list = []
for day in df_copy.day.sort_values().unique():
    df_day_list.append(df_copy.loc[df_copy.day == day, ['latitud', 'longitud', 'cantidad']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist())

In [ ]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=12)
HeatMapWithTime(df_day_list, radius=5, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.5, max_opacity=0.8, use_local_extrema=True).add_to(base_map)
base_map

In [ ]:
df_week_list = []
for week in df_copy.week.sort_values().unique():
    df_week_list.append(df_copy.loc[df_copy.week == week, ['latitud', 'longitud', 'cantidad']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist())

In [ ]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=12)
HeatMapWithTime(df_week_list, radius=5, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.5, max_opacity=0.8, use_local_extrema=True).add_to(base_map)
base_map

In [ ]:
df_hour_list = []
for hour in df_copy.hour.sort_values().unique():
    df_hour_list.append(df_copy.loc[df_copy.hour == hour, ['latitud', 'longitud', 'cantidad']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist())

In [ ]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=12)
HeatMapWithTime(df_hour_list, radius=8, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.5, max_opacity=0.8, use_local_extrema=True).add_to(base_map)
base_map

In [ ]:
df_copy.head()